<a href="https://colab.research.google.com/github/HausReport/ClubRaiders/blob/master/notebooks/History.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import sys

!{sys.executable} -m pip install --force-reinstall --upgrade "git+https://github.com/HausReport/ClubRaiders.git#egg=craid"
import craid.eddb.loader.DataProducer as dp
import pandas as pd
import logging
import plotly.graph_objs as go
import plotly.express as px
import numpy as np
from dateutil.relativedelta import relativedelta
from datetime import timedelta, date


logging.getLogger().addHandler(logging.StreamHandler())
logging.getLogger().level = logging.DEBUG

arrays = dp.getDataArrays()
baseFrame: pd.DataFrame = arrays['dataFrame']

  Cloning https://github.com/HausReport/ClubRaiders.git to /tmp/pip-install-c9q5kbwp/craid
  Running command git clone -q https://github.com/HausReport/ClubRaiders.git /tmp/pip-install-c9q5kbwp/craid
Processing /root/.cache/pip/wheels/8f/56/d1/def235a9ef977abf4476d1ad7a3ad8d9af7537445ce01c5e16/dash-1.16.3-cp36-none-any.whl
Processing /root/.cache/pip/wheels/29/11/a0/0cf8183b6f7df4716bec25b0e089043cd161bb58accc6633a6/dash_core_components-1.12.1-cp36-none-any.whl
Processing /root/.cache/pip/wheels/8d/01/46/78e4de185a8a4a2da8ba31da16c52170f036d4cebeeb6e07a2/dash_html_components-1.1.1-cp36-none-any.whl
Processing /root/.cache/pip/wheels/3d/c2/fd/50a7ea0b9aef63cf3bf3c5fb22799b8ba9a97ea8f9b14b7124/dash_table-4.10.1-cp36-none-any.whl
Processing /root/.cache/pip/wheels/c8/8f/0f/9cf71e7362b302350e10fcc9ca7f0377b84a6ea14445c2d6aa/dash_renderer-1.8.2-cp36-none-any.whl
  Using cached https://files.pythonhosted.org/packages/f2/28/2a03252dfb9ebf377f40fba6a7841b47083260bf8bd8e737b0c6952df83f/Flask-1.

Acquired lock.
Loading from AWS
Memory tracker: 0:166,858,752
Found data file: /tmp/smol-factions.jsonl.gz
Read 626 lines of faction data
Memory tracker: 0.5:167,428,096
Found data file: /tmp/smol-systems_populated.jsonl.gz
Read 165 lines of systems data
Memory tracker: 1:169,582,592
Populated club system keys
Club system lookup set has {165} items
Populated faction instances: {991} items.
Memory tracker: 2:170,778,624
Found data file: /tmp/smol-stations.jsonl.gz
Read 544 lines of station data, adding 544
Memory tracker: 3:171,315,200
station controlling faction doesn't exist: Qwent Research Base
station controlling faction doesn't exist: Qwent Research Base
station controlling faction doesn't exist: Qwent Research Base
station controlling faction doesn't exist: Qwent Research Base
station controlling faction doesn't exist: Qwent Research Base
station controlling faction doesn't exist: Qwent Research Base
station controlling faction doesn't exist: Qwent Research Base
station controllin

In [2]:
#pip install "pandas-profiling"


In [3]:
from craid.eddb.loader.strategy.DataLoader import DataLoader
from craid.eddb.loader.strategy.GithubLoader import LoadDataFromGithub
from craid.history.History import History

myLoader = LoadDataFromGithub(_forceWebDownload=True, useSmol=False)
hist = History()
csa = hist.getRawDataFrame()
target = hist.getNormalizedDataFrame()

Found data file: /tmp/history.jsonl.gz
NumExpr defaulting to 2 threads.
Read system        17652
faction       17652
updated       17652
influence     17652
control       17652
region        17652
population    17652
dtype: int64 lines of history data


Creating the object


In [4]:
def getScroller(fig):
  fig.update_layout(
    xaxis=dict(
        rangeselector=dict(
            buttons=list([
                dict(count=1,
                     label="1m",
                     step="month",
                     stepmode="backward"),
                dict(count=6,
                     label="6m",
                     step="month",
                     stepmode="backward"),
                dict(count=1,
                     label="YTD",
                     step="year",
                     stepmode="todate"),
                dict(count=1,
                     label="1y",
                     step="year",
                     stepmode="backward"),
                dict(step="all")
            ])
        ),
        rangeslider=dict(
            visible=True
        ),
        type="date"
  ))

In [5]:
def getFactionInfluenceGraph(fac: str):
  ogun = target[ target['faction']==fac]
  a = ogun['system'].unique().tolist()
  fig = go.Figure()
  for sys in a:
    theSlice = ogun[ ogun['system'] == sys].reset_index()
    fig.add_trace(go.Scatter(x=theSlice['updated'], y=theSlice['influence'],
                    mode='lines',
                    stackgroup="b",
                    name=sys,
                    stackgaps='interpolate'))
  getScroller(fig)
  return fig

In [6]:
def getSystemInfluenceGraph(sys: str):
  ogun = target[ target['system']==sys]
  a = ogun['faction'].unique().tolist()
  fig = go.Figure()
  for fac in a:
    theSlice = ogun[ ogun['faction'] == fac].reset_index()
    fig.add_trace(go.Scatter(x=theSlice['updated'], y=theSlice['influence'],
                    mode='lines',
                    name=fac))
  getScroller(fig)
  return fig

In [7]:
# data cleaning
# done in api now
#csa = csa.drop_duplicates()
#csa = csa[ csa['faction'] != 'Aegis of Federal Democrats']
#csa = csa[ csa['faction'] != 'Aegis Imperium']
#csa = csa[ csa['faction'] != "Emperor's Dawn"]

In [8]:
stage1 = csa.loc[csa.groupby(['faction','system']).updated.idxmax()]
stage3 = stage1[['system','faction','influence']].groupby('faction').influence.sum().reset_index()
fig = px.pie(stage3, values='influence', names='faction', title='Total Influence by Minor Faction', width=350, height=350)
fig.update_traces(textposition="inside")
fig.update_layout(showlegend=False)
fig.show()

In [9]:
from craid.club.regions.RegionFactory import RegionFactory
stage3 = stage1[['region','influence']].groupby('region').influence.sum().reset_index()
regionNames = list(RegionFactory.regionDict.keys())
#fig = px.pie(stage3, values='influence', names=regionNames, title='Total Club Influence by Region', width=350, height=350) #, names='faction'
#fig.update_traces(textposition="inside")
#fig.update_layout(showlegend=False)
#fig.show()

In [10]:
region = 1
regionNames = list(RegionFactory.regionDict.keys())
regionName = regionNames[region]
title = f"Total Influence <br>by Minor Faction <br>in the {regionName} region"
merope = target[ target['region']== region]
stage1 = merope.loc[merope.groupby(['faction','system']).updated.idxmax()]
stage3 = stage1[['system','faction','influence']].groupby('faction').influence.sum().reset_index()
fig = px.pie(stage3, values='influence', names='faction', title=title, width=350, height=350) #, names='faction'
fig.update_traces(textposition="inside")
fig.update_layout(showlegend=False)
fig.show()

In [11]:
theDate = '2020-06-1'
#reg = csa[ csa['region']== 1]
dated = csa [ csa['updated']<= theDate]

stage1 = dated.loc[dated.groupby(['faction','system']).updated.idxmax()]
#stage1[['system','faction','influence']]
stage3 = stage1[['system','faction','influence']].groupby('faction').influence.sum().reset_index()
stage3.influence.sum()

4236.007999040682

In [12]:
region = 8

dates = []
inf = []

start_date = date(2018, 5, 15)
daily_date = date(2020,5,30)
end_date = date.today() + timedelta(days=1) 

dframe = csa[ csa['region'] == region]
regionNames = list(RegionFactory.regionDict.keys())
regionName = regionNames[region]
title = f"Total Club Influence in the {regionName} region"

single_date = start_date
while single_date <= end_date:
    theDate = single_date.strftime("%Y-%m-%d")
    dated = dframe [ dframe['updated']<= theDate]

    stage1 = dated.loc[dated.groupby(['faction','system']).updated.idxmax()]
    stage3 = stage1[['system','faction','influence']].groupby('faction').influence.sum().reset_index()
    theInf = stage3.influence.sum()
    dates.append(theDate)
    inf.append(theInf)
    if(single_date<daily_date):
      single_date = single_date + relativedelta(months=1)
    else:
      single_date = single_date + relativedelta(days=1)
      
labels = {'x':'Day', 'y':"Total Influence"}
fig = px.line(x=dates, y=inf, title=title, labels=labels)
fig.show()

In [13]:

dates = []
inf = []

start_date = date(2018, 5, 15)
daily_date = date(2020,5,30)
end_date = date.today() + timedelta(days=1) 

dframe = csa
regionNames = list(RegionFactory.regionDict.keys())
regionName = regionNames[region]
title = f"Total Club Influence"

single_date = start_date
while single_date <= end_date:
    theDate = single_date.strftime("%Y-%m-%d")
    dated = dframe [ dframe['updated']<= theDate]

    stage1 = dated.loc[dated.groupby(['faction','system']).updated.idxmax()]
    stage3 = stage1[['system','faction','influence']].groupby('faction').influence.sum().reset_index()
    theInf = stage3.influence.sum()
    dates.append(theDate)
    inf.append(theInf)
    if(single_date<daily_date):
      single_date = single_date + relativedelta(months=1)
    else:
      single_date = single_date + relativedelta(days=1)

labels = {'x':'Day', 'y':"Total Influence"}
fig = px.line(x=dates, y=inf, title=title, labels=labels)
fig.show()

In [14]:
dates = []
inf = []

faction = "Sirius Corporation"
faction = "Hodack Prison Colony"
faction = "Wreaken Construction"
#faction = "'Sirius Drives'"
faction = "Aegis Core"
#faction = "Aegis Research"
#faction = "Bill Turner"

start_date = date(2018, 5, 15)
daily_date = date(2020,5,30)
end_date = date.today() + timedelta(days=1) #date(2020, 6, 28)


dframe = csa[ csa['faction'] == faction]
regionNames = list(RegionFactory.regionDict.keys())
regionName = regionNames[region]
title = f"Total Influence of the {faction} Faction"

single_date = start_date
while single_date <= end_date:
    theDate = single_date.strftime("%Y-%m-%d")
    dated = dframe [ dframe['updated']<= theDate]

    stage1 = dated.loc[dated.groupby(['faction','system']).updated.idxmax()]
    stage3 = stage1[['system','faction','influence']].groupby('faction').influence.sum().reset_index()
    theInf = stage3.influence.sum()
    dates.append(theDate)
    inf.append(theInf)
    if(single_date<daily_date):
      single_date = single_date + relativedelta(months=1)
    else:
      single_date = single_date + relativedelta(days=1)


labels = {'x':'Day', 'y':"Total Influence"}
fig = px.line(x=dates, y=inf, title=title, labels=labels)
fig.show()

In [15]:
getFactionInfluenceGraph("Aegis Core").show()

In [16]:
badGuys= ['Abroin Universal PLC',
                     'Aegis Core', 'Aegis Defense', 'Aegis Research',
                      'Bill Turner',
                     'CQC Holdings',
                     'Gallant Investment Brokers', 'Hodack Prison Colony',
                     'Janus Incorporated', "Namarii Emperor's Dawn",
                     'Pleiades Resource Enterprise',
                     'Reyan BPS', 'Reynhardt IntelliSys',
                     'Sirius Atmospherics', 'Sirius Catering', 'Sirius Corporation',
                     'Sirius Drives', 'Sirius Hot2Cold', 'Sirius Hyperspace',
                     'Sirius Industrial', 'Sirius Luxury Transports', 'Sirius Mining Merope',
                     'Sirius Mining', 'Sirius Power',
                     'The Greenventure Group',
                     'The Peterson Group', 'The Rockforth Corporation',
                     'Turner Research Group', 'Wiggins Development Trust',
                     'Wreaken Construction'
                     ]

In [17]:
a = csa['faction'].unique().tolist()
b = baseFrame['factionName'].unique().tolist()
aa = set(a)
bb = set(b)
bb-aa

set()

In [18]:
dates = []
inf = []

faction = "Combined Sirius Factions"
faction1 = "Sirius"

start_date = date(2018, 5, 15)
daily_date = date(2020,5,30)
end_date = date.today() + timedelta(days=1) #date(2020, 6, 28)


dframe = target[ (target['faction'].str.contains(faction1)) ]
regionNames = list(RegionFactory.regionDict.keys())
regionName = regionNames[region]
title = f"Total Influence of the {faction} Faction"

single_date = start_date
while single_date <= end_date:
    theDate = single_date.strftime("%Y-%m-%d")
    dated = dframe [ dframe['updated']<= theDate]

    stage1 = dated.loc[dated.groupby(['faction','system']).updated.idxmax()]
    stage3 = stage1[['system','faction','influence']].groupby('faction').influence.sum().reset_index()
    theInf = stage3.influence.sum()
    dates.append(theDate)
    inf.append(theInf)
    if(single_date<daily_date):
      single_date = single_date + relativedelta(months=1)
    else:
      single_date = single_date + relativedelta(days=1)


labels = {'x':'Day', 'y':"Total Influence"}
fig = px.line(x=dates, y=inf, title=title, labels=labels)
fig.show()

In [19]:
# One System, handles Multiple Factions
fig = getSystemInfluenceGraph("Celaeno")
fig.show()

In [20]:
fig = getSystemInfluenceGraph("Solati")
fig.show()

In [21]:
# One System, handles Multiple Factions
fig = getSystemInfluenceGraph("Sol")
fig.show()

In [22]:
fac = "Hodack Prison Colony"
ogun = target[ target['faction']==fac]
a = ogun['system'].unique().tolist()
fig = go.Figure()
for sys in a:
  theSlice = ogun[ ogun['system'] == sys].reset_index()
  fig.add_trace(go.Scatter(x=theSlice['updated'], y=theSlice['influence'],
                    mode='lines',
                    name=sys,
                    stackgroup="one",
                    stackgaps="interpolate"))

getScroller(fig)
fig.show()


In [23]:
getFactionInfluenceGraph('Hodack Prison Colony').show()

In [24]:
fac = 'Sirius Mining'


fac = 'Aegis Core'
fac = 'Sirius Mining Merope'
fac = 'CQC Holdings'
getFactionInfluenceGraph(fac).show()

In [25]:
from typing import List
def getCombinedFactionGraph( factions: List[str], titleSubject=None):
  labels = {'x':'Day', 'y':"Total Influence"}
  fig = go.Figure()
  for fac in factions:
    foo = target[target['faction']== fac]
    stage3 = foo[['system','faction','influence','updated']].groupby(['updated']).influence.sum().reset_index()
    fig.add_trace(go.Scatter(x=stage3['updated'], y=stage3['influence'],
                    mode='lines',
                    stackgroup="b",
                    name=fac,
                    stackgaps="interpolate"))

  if titleSubject is None:
    titleSubject = "+".join(factions)

  title = f"Total influence of {titleSubject}"
  fig.update_layout(title=title,
                    xaxis_title="Date",
                    yaxis_title="Total Influence")
  getScroller(fig)
  return fig



In [26]:
factions = ["Wreaken Construction", "Hodack Prison Colony"]

fig = getCombinedFactionGraph( factions, titleSubject=None)
fig.show()

In [27]:
siriusFactions = ['Sirius Atmospherics', 'Sirius Catering',
       'Sirius Corporation', 'Sirius Drives', 'Sirius Hot2Cold',
       'Sirius Hyperspace', 'Sirius Industrial',
       'Sirius Luxury Transports', 'Sirius Mining Merope',
       'Sirius Mining', 'Sirius Power']
      
fig = getCombinedFactionGraph( siriusFactions, titleSubject="Combined Sirius Factions")
fig.show()

In [28]:
csa = hist.getRawDataFrame()[['system','faction','updated','influence']]
display(csa)

system  ...  influence
0                         Abroin  ...  49.849500
1                         Abroin  ...  45.600000
2                         Abroin  ...  46.750567
3                         Abroin  ...  59.000000
4                         Abroin  ...  54.700000
...                          ...  ...        ...
17647        Synuefe YM-H d11-84  ...  29.129100
17648                  HIP 17655  ...  16.267500
17649  California Sector BV-Y c7  ...  10.721400
17650                     Delphi  ...   7.591100
17651                     Delphi  ...   5.364400

[17652 rows x 4 columns]

In [29]:
csa.columns

Index(['system', 'faction', 'updated', 'influence'], dtype='object')

In [30]:
#csa = csa.rename(columns={'system':'string', 'faction':'string', 'updated':'datetime', 'influence':'float', 'control':'boolean', 'region':'int','population':'float'})
csa = csa.rename(columns={'int':'id',
                          'string':'system',
                          'string':'faction',
                          'datetime': 'updated', 
                          'float':'influence',
                          'boolean':'control',
                          'int':'region',
                          'float': 'population'})

In [31]:
csa

system  ...  influence
0                         Abroin  ...  49.849500
1                         Abroin  ...  45.600000
2                         Abroin  ...  46.750567
3                         Abroin  ...  59.000000
4                         Abroin  ...  54.700000
...                          ...  ...        ...
17647        Synuefe YM-H d11-84  ...  29.129100
17648                  HIP 17655  ...  16.267500
17649  California Sector BV-Y c7  ...  10.721400
17650                     Delphi  ...   7.591100
17651                     Delphi  ...   5.364400

[17652 rows x 4 columns]

In [32]:
csa['system'].replace('', np.nan, inplace=True)
csa['faction'].replace('', np.nan, inplace=True)
csa['updated'].replace('', np.nan, inplace=True)
csa['influence'].replace('', np.nan, inplace=True)

In [33]:
pd.set_option('mode.chained_assignment', None)


In [34]:
from craid.eddb.loader.strategy.AWSLoader import LoadDataFromAWS
loader = LoadDataFromAWS(forceWebDownload=False, useSmol=False)
fName = loader.find_data_file('history.jsonl')
dataframe = pd.read_json(fName, lines=True, compression='infer')
dataframe = dataframe[ dataframe.faction != "Benton's Gang"]
dataframe = dataframe[ dataframe.faction != "Bentonian Party"]
dataframe = dataframe[ dataframe.faction != "Worster Insurance"]



Found data file: /tmp/history.jsonl.gz


In [35]:
csa.attrs

{}

In [36]:
dataframe = dataframe.rename(columns={'string':'system',
                          'string':'faction',
                          'datetime': 'updated', 
                          'float':'influence',
                          'boolean':'control',
                          'int':'region',
                          'float': 'population'})

In [37]:
pd.set_option('max_rows', 99999)
pd.set_option('max_colwidth', 400)

In [38]:
dataframe

system  ...   population
0                            Abroin  ...            0
1                            Abroin  ...            0
2                            Abroin  ...            0
3                            Abroin  ...            0
4                            Abroin  ...            0
5                            Abroin  ...            0
6                            Abroin  ...            0
7                            Abroin  ...            0
8                            Abroin  ...            0
9                            Abroin  ...            0
10                           Abroin  ...            0
11                           Abroin  ...            0
12                           Abroin  ...            0
13                           Abroin  ...            0
14                           Abroin  ...            0
15                           Abroin  ...            0
16                           Abroin  ...            0
17                           Abroin  ...            0
18                           Baiame  ...            0
19                           Baiame  ...            0
20                           Baiame  ...            0
21                           Baiame  ...            0
22                           Baiame  ...            0
23                           Baiame  ...            0
24                           Baiame  ...            0
25                           Baiame  ...            0
26                          Carunda  ...            0
27                          Carunda  ...            0
28                          Carunda  ...            0
29                          Carunda  ...            0
30                          Carunda  ...            0
31                          Carunda  ...            0
32                          Carunda  ...            0
33                          Carunda  ...            0
34                        HIP 66267  ...            0
35                        HIP 66267  ...            0
36                        HIP 66267  ...            0
37                        HIP 67109  ...            0
38                        HIP 67109  ...            0
39                        HIP 67109  ...            0
40                        HIP 67109  ...            0
41                        HIP 67109  ...            0
42                        HIP 67109  ...            0
43                        HIP 67109  ...            0
44                        HIP 67109  ...            0
45                        HIP 67109  ...            0
46                        HIP 67109  ...            0
47                        HIP 67109  ...            0
48                        HIP 68796  ...            0
49                        HIP 68796  ...            0
50                        HIP 68796  ...            0
51                        HIP 68796  ...            0
52                        HIP 68796  ...            0
53                        HIP 68796  ...            0
54                        HIP 69767  ...            0
55                        HIP 69767  ...            0
56                        HIP 69767  ...            0
57                        HIP 69767  ...            0
58                        HIP 69767  ...            0
59                        HIP 69767  ...            0
60                        HIP 69767  ...            0
61                        HIP 69767  ...            0
62                        HIP 69767  ...            0
63                        HIP 69767  ...            0
64                        HIP 69767  ...            0
65                        HIP 69767  ...            0
66                        HIP 70255  ...            0
67                        HIP 70255  ...            0
68                        HIP 70255  ...            0
69                        HIP 70255  ...            0
70                        HIP 70255  ...            0
71                        HIP 72726  ...            0
72                        HIP 72726  ...            0
73                        HIP 727

In [39]:
getFactionInfluenceGraph("Sirius Mining Merope").show()

In [40]:
getFactionInfluenceGraph("Sirius Hyperspace").show()

In [41]:
getFactionInfluenceGraph("Pleiades Resource Enterprise").show()

In [42]:
df_fac = dataframe.faction.unique().tolist()

def Diff(li1, li2): 
    li_dif = [i for i in li1 + li2 if i not in li1 or i not in li2] 
    return li_dif 

Diff(df_fac, badGuys)

[]

In [43]:
#tf = csa[aegis & october]
tf = dataframe
tf = tf.reset_index()
tf = tf.sort_values( ['system','updated'])
tf = tf.rename(columns={'string':'system',
                          'string':'faction',
                          'timestamp': 'updated', 
                          'float':'influence',
                          'boolean':'control',
                          'int':'region',
                          'float': 'population'})
tf['updated'] = pd.to_datetime(tf.updated, unit='ms')
tf['updated'] = tf.updated.dt.round('D')
tf = tf.drop_duplicates(subset=['system', 'faction', 'updated'])
target = tf

#mf = tf
##mf['updated'] = tf.updated.dt.round('MS')
#mf['updated'] = pd.to_datetime(mf.updated).dt.to_period('M').dt.to_timestamp()
#mf = mf.drop_duplicates(subset=['system', 'faction', 'updated'])
#hurm = mf.groupby(['updated','faction']).count().reset_index()
#hurm

In [80]:
def factionPresenceGraph( faction: str):

  #
  # Narrow down part of dataframe you want here
  #
  #mf = dataframe.copy()
  mf = dataframe[dataframe['faction']== faction].copy()


  #
  # Convert to monthly and clean
  #
  mf['updated'] = pd.to_datetime(mf.updated, unit='ms')
  mf['updated'] = pd.to_datetime(mf.updated).dt.to_period('W').dt.to_timestamp()
  mf = mf.drop_duplicates(subset=['system', 'faction', 'updated'])
  hurm = mf.groupby(['updated','faction']).count().reset_index()

  labels = {'x':'Day', 'y':"Total Systems"}
  #foo = hurm[hurm['faction']== faction]
  foo = hurm
  fig = go.Figure(data=go.Scatter(x=foo.updated, y=foo.system, mode='lines+markers'))

  #fig = go.Figure()
  #factions = hurm['faction'].unique().tolist()
  #for fac in factions:
  #  foo = hurm[hurm['faction']== fac]
  #  stage3 = foo[['system','faction','updated']].groupby(['updated']).count().reset_index()
  #  fig.add_trace(go.Scatter(x=stage3['updated'], y=stage3['count'],
  #                  mode='lines',
  #                  stackgroup="b",
  #                  name=fac,
  #                  stackgaps="interpolate"))

  #if titleSubject is None:
  #  titleSubject = "+".join(factions)

  title = f"System Presences of {faction}"
  fig.update_layout(title=title,
                    xaxis_title="Date",
                    yaxis_title="Total Systems")
  #getScroller(fig)
  return fig

In [52]:
  mf = dataframe.copy()
  mf['updated'] = pd.to_datetime(mf.updated).dt.to_period('M').dt.to_timestamp()
  mf = mf.drop_duplicates(subset=['system', 'faction', 'updated'])
  hurm = mf.groupby(['updated','faction']).count().reset_index()
  hurm

updated                       faction  ...  region  population
0  1970-01-01          Abroin Universal PLC  ...      13          13
1  1970-01-01                    Aegis Core  ...       3           3
2  1970-01-01                 Aegis Defense  ...       3           3
3  1970-01-01                Aegis Research  ...      31          31
4  1970-01-01                   Bill Turner  ...       1           1
5  1970-01-01                  CQC Holdings  ...      25          25
6  1970-01-01    Gallant Investment Brokers  ...       2           2
7  1970-01-01          Hodack Prison Colony  ...      23          23
8  1970-01-01            Janus Incorporated  ...      21          21
9  1970-01-01        Namarii Emperor's Dawn  ...       2           2
10 1970-01-01  Pleiades Resource Enterprise  ...      12          12
11 1970-01-01                     Reyan BPS  ...       1           1
12 1970-01-01          Reynhardt IntelliSys  ...       1           1
13 1970-01-01           Sirius Atmospherics  ...       2           2
14 1970-01-01               Sirius Catering  ...       1           1
15 1970-01-01            Sirius Corporation  ...      26          26
16 1970-01-01                 Sirius Drives  ...       4           4
17 1970-01-01               Sirius Hot2Cold  ...       4           4
18 1970-01-01             Sirius Hyperspace  ...       8           8
19 1970-01-01             Sirius Industrial  ...       1           1
20 1970-01-01      Sirius Luxury Transports  ...      16          16
21 1970-01-01                 Sirius Mining  ...       9           9
22 1970-01-01          Sirius Mining Merope  ...       7           7
23 1970-01-01                  Sirius Power  ...       1           1
24 1970-01-01        The Greenventure Group  ...       1           1
25 1970-01-01            The Peterson Group  ...       1           1
26 1970-01-01     The Rockforth Corporation  ...       1           1
27 1970-01-01         Turner Research Group  ...       8           8
28 1970-01-01     Wiggins Development Trust  ...       1           1
29 1970-01-01          Wreaken Construction  ...      10          10

[30 rows x 7 columns]

In [66]:
factionPresenceGraph("Pleiades Resource Enterprise")

In [81]:
factionPresenceGraph("Sirius Mining Merope")

In [68]:
factionPresenceGraph("Sirius Hyperspace")

In [78]:
def regionPresenceGraph( faction: str):

  #
  # Narrow down part of dataframe you want here
  #
  #mf = dataframe.copy()
  mf = dataframe[dataframe['region']== 1].copy()


  #
  # Convert to monthly and clean
  #
  mf['updated'] = pd.to_datetime(mf.updated, unit='ms')
  mf['updated'] = pd.to_datetime(mf.updated).dt.to_period('W').dt.to_timestamp()
  mf = mf.drop_duplicates(subset=['system', 'faction', 'updated'])
  hurm = mf.groupby(['updated']).count().reset_index()

  labels = {'x':'Day', 'y':"Total Systems"}
  #foo = hurm[hurm['faction']== faction]
  foo = hurm
  fig = go.Figure(data=go.Scatter(x=foo.updated, y=foo.system, mode='lines+markers'))

  #fig = go.Figure()
  #factions = hurm['faction'].unique().tolist()
  #for fac in factions:
  #  foo = hurm[hurm['faction']== fac]
  #  stage3 = foo[['system','faction','updated']].groupby(['updated']).count().reset_index()
  #  fig.add_trace(go.Scatter(x=stage3['updated'], y=stage3['count'],
  #                  mode='lines',
  #                  stackgroup="b",
  #                  name=fac,
  #                  stackgaps="interpolate"))

  #if titleSubject is None:
  #  titleSubject = "+".join(factions)

  title = f"System Presences of {faction}"
  fig.update_layout(title=title,
                    xaxis_title="Date",
                    yaxis_title="Total Systems")
  #getScroller(fig)
  return fig

In [79]:
regionPresenceGraph("Sirius Hyperspace")

In [75]:
  mf = dataframe[dataframe['region']== 1].copy()


  #
  # Convert to monthly and clean
  #
  mf['updated'] = pd.to_datetime(mf.updated, unit='ms')
  mf['updated'] = pd.to_datetime(mf.updated).dt.to_period('M').dt.to_timestamp()
  #mf = mf[ mf.loc[mf.groupby(['system','faction','updated').B.idxmin()]
  mf = mf.drop_duplicates(subset=['system', 'faction', 'updated'])
  hurm = mf.groupby(['updated']).count().reset_index()
hurm

updated  system  faction  influence  control  region  population
0  2017-10-01       1        1          1        1       1           1
1  2018-05-01      48       48         48       48      48          48
2  2018-06-01      47       47         47       47      47          47
3  2018-07-01      47       47         47       47      47          47
4  2018-08-01      47       47         47       47      47          47
5  2018-09-01      49       49         49       49      49          49
6  2018-10-01      48       48         48       48      48          48
7  2018-11-01      49       49         49       49      49          49
8  2018-12-01      51       51         51       51      51          51
9  2019-01-01      51       51         51       51      51          51
10 2019-02-01      51       51         51       51      51          51
11 2019-03-01      49       49         49       49      49          49
12 2019-04-01      48       48         48       48      48          48
13 2019-05-01      48       48         48       48      48          48
14 2019-06-01      48       48         48       48      48          48
15 2019-07-01      48       48         48       48      48          48
16 2019-08-01      46       46         46       46      46          46
17 2019-09-01      46       46         46       46      46          46
18 2019-10-01      46       46         46       46      46          46
19 2019-11-01      45       45         45       45      45          45
20 2019-12-01      45       45         45       45      45          45
21 2020-01-01      43       43         43       43      43          43
22 2020-02-01      42       42         42       42      42          42
23 2020-03-01      42       42         42       42      42          42
24 2020-04-01      42       42         42       42      42          42
25 2020-05-01      42       42         42       42      42          42
26 2020-06-01      41       41         41       41      41          41
27 2020-07-01      29       29         29       29      29          29
28 2020-08-01      37       37         37       37      37          37
29 2020-09-01      33       33         33       33      33          33
30 2020-10-01      30       30         30       30      30          30